In [1]:
import pandas as pd
import sys
import random
import os
from pathlib import Path
import shutil
import json

import argparse
from tqdm import tqdm
import spacy
from spacy.gold import minibatch
from spacy.language import Language
from spacy import util

from scispacy.data_util import read_full_med_mentions, read_ner_from_tsv
from scispacy.util import WhitespaceTokenizer
from scispacy.per_class_scorer import PerClassScorer
from scispacy.train_utils import evaluate_ner
from ast import literal_eval
import itertools
import re
# import gensim

In [2]:
data_path = '/nfs/misc/literature/maaly/metagenome/data/csv/ENA_MIBIG_compound_EMBD_fasttext_200_5_TAGD.csv'
data_df = pd.read_csv(data_path,names=['index','pmc_id','sentence','doc_score','entities', 'entity_scores'], header = 1)

In [3]:
df_ = data_df[['pmc_id','sentence','doc_score','entities', 'entity_scores']]
df = df_[df_['doc_score']<0.30]
df.head(10)

pmc_id                                           sentence  doc_score  \
1   PMC100051                  Hydroxystreptomycin biosynthesis.       0.20   
6   PMC101490  Notably, as expected, all Thior Strr colonies ...       0.28   
9   PMC100051  Both proteins are involved in the synthesis of...       0.20   
10  PMC101490  (Recombinants sensitive to both apramycin and ...       0.27   
14  PMC101490  Conjugal transfer of the entire actinorhodin g...       0.24   
15  PMC100051                  Hydroxystreptomycin biosynthesis.       0.20   
17  PMC101490  pHU207 is a derivative of pHU205 that also inc...       0.27   
22  PMC101600  The thin-layer chromatogram showed the accumul...       0.28   
25  PMC101600  Identified ORFs in the biosynthetic gene clust...       0.29   
27  PMC101600  While coumermycin A1 production in the wild-ty...       0.23   

                                      entities      entity_scores  
1                      ['Hydroxystreptomycin']             [0.28]  
6                             ['actinorhodin']             [0.21]  
9   ['aminocoumarin', 'novobiocin', 'noviose']  [0.17, 0.2, 0.29]  
10                            ['streptomycin']             [0.22]  
14              ['actinorhodin', 'derivative']       [0.21, 0.29]  
15                     ['Hydroxystreptomycin']             [0.28]  
17                              ['derivative']             [0.29]  
22                             ['coumermycin']             [0.14]  
25                             ['coumermycin']             [0.14]  
27              ['coumermycin', 'coumermycin']       [0.14, 0.14]

In [4]:
def filter_tags_in_range(dict_entities, lower_limit, upper_limit):
    entities =[]
# Iterate over all the items in dictionary and filter items which has even keys
    for (key, value) in dict_entities.items():
        if lower_limit <= value <= upper_limit:
            entities.append(key)
    return entities

def filter_tags(dict_entities):
    entities =[]
# Iterate over all the items in dictionary and filter items which has even keys
    for (key, value) in dict_entities.items():
        if value < 0.28:
            entities.append(key)
    return entities

def find_span(tag,sentence):
    all_spans =[]
    try:
        for match in re.finditer(tag, sentence):
            all_spans.append(match.span())

        if all_spans:
            return all_spans[0]
        else:
            return False
    except:
        return False

 

In [5]:
list_range = [(107, 116)]

def test_range(n_span, list_range):
    for each_item in list_range:
        if n_span[0] in range(each_item[0]-1,each_item[1]+1):
            return True
            break
   
    for each_item in list_range:
        if n_span[1] in range(each_item[0]-1,each_item[1]+1):
            return True
            break

    return False
    
    
test_range((4, 11), [(0,12)])   

True

In [6]:
# training_data = []
# label = 'BGC'

# for iter_1, each_annotation in tqdm(df.iterrows(), total=df.shape[0]):
# #         print('hello')
#     text = each_annotation['sentence']
#     entities = []
# #     ner = filter_tags(literal_eval(each_annotation['entities']))
#     ner = literal_eval(each_annotation['entities'])
#     if ner:
#         check_spans_bucket =[]
#         for each_ner in ner:
#             spanner = find_span(each_ner,text)
#             if spanner:
#                 if not test_range(spanner, check_spans_bucket): # there are overlapping texts
#                     entities.append((spanner[0], spanner[1],label))
#                 check_spans_bucket.append(spanner)
#             else:
#                 pass
            
#         if entities:
#             training_data.append((text, {"entities" : entities}))
            


In [7]:
def convert_Maalys_format_to_spacy_format(dataframe):
    
    training_data = []
    devel_data = []
    test_data =[]
    
    label = 'BGC'
    
    for iter_index, each_annotation in tqdm(dataframe.iterrows(), total=dataframe.shape[0]):
    #         print('hello')
        text = each_annotation['sentence']
        entities = []
#         ner = filter_tags(literal_eval(each_annotation['entities']))
        ner = literal_eval(each_annotation['entities'])
        if ner:
            check_spans_bucket =[]
            for each_ner in ner:
                spanner = find_span(each_ner,text)
                if spanner:
                    if not test_range(spanner, check_spans_bucket): # there are overlapping texts
                        entities.append((spanner[0], spanner[1],label))
                    check_spans_bucket.append(spanner)
                else:
                    pass

            if entities:
                    training_data.append((text, {"entities" : entities}))
            

    return training_data


training_data = convert_Maalys_format_to_spacy_format(df)

100%|██████████| 3250123/3250123 [08:15<00:00, 6561.57it/s]


# Dont run this every time

In [8]:
# # Convert fastext embeddings to Spacyformat


# from gensim.models.fasttext import FastText
# import sys

# model_path = '/nfs/misc/literature/maaly/metagenome/python/scripts/ML/word2vec/metagenomics_fasttext_200_5.model'
# out_file = '/nfs/gns/literature/Santosh_Tirunagari/pretrained_word_embeddings/Data/metagenomics_fasttext/'
# model = FastText.load(model_path)

# print("embedding dim: {}".format(model.wv.vector_size))
# print("vocab size:{}".format(len(model.wv.vocab)))

# with open(out_file, 'w') as f:
#     f.write(f"{len(model.wv.vocab)} {model.wv.vector_size}\n")
#     for word in model.wv.vocab:
#         f.write(f"{word} {' '.join(map(str, model.wv[word].tolist()))}\n")

In [9]:
# # convert fastext format to spaCy format
# # Dont run this it will take a loy of time

# !python -m spacy init-model en /nfs/gns/literature/Santosh_Tirunagari/pretrained_word_embeddings/models/en-metgenomics-lg --vectors-loc /nfs/gns/literature/Santosh_Tirunagari/pretrained_word_embeddings/Data/metagenomics_fasttext/metagenomics_fasttext.txt.gz

In [10]:
def train_ner(output_dir: str,
              train_data,
              dev_data,
              test_data,
              run_test: bool = None,
              model: str = None,
              n_iter: int = 10,
              meta_overrides: str = None):

    util.fix_random_seed(util.env_opt("seed", 0))
    os.makedirs(output_dir, exist_ok=True)
    if run_test:
        nlp = spacy.load(model)
        print("Loaded model '%s'" % model)
        evaluate_ner(nlp, dev_data, dump_path=os.path.join(output_dir, "dev_metrics.json"))
        evaluate_ner(nlp, test_data, dump_path=os.path.join(output_dir, "test_metrics.json"))
    else:
        train(model, train_data, dev_data, test_data, output_dir, n_iter, meta_overrides)

In [11]:
def train(model, train_data, dev_data, test_data, output_dir, n_iter, meta_overrides):
    """Load the model, set up the pipeline and train the entity recognizer."""
    
    if model is not None:
        nlp = spacy.load(model)  # load existing spaCy model
        print("Loaded model '%s'" % model)
    else:
        nlp = spacy.blank('en')  # create blank Language class
        print("Created blank 'en' model")

    if meta_overrides is not None:
        metadata = json.load(open(meta_overrides))
        nlp.meta.update(metadata)

    original_tokenizer = nlp.tokenizer

    nlp.tokenizer = WhitespaceTokenizer(nlp.vocab)

    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if 'ner' not in nlp.pipe_names and "parser" in nlp.pipe_names:
        ner = nlp.create_pipe('ner')
        nlp.add_pipe(ner, after="parser")
    elif 'ner' not in nlp.pipe_names and "tagger" in nlp.pipe_names:
        ner = nlp.create_pipe('ner')
        nlp.add_pipe(ner, after="tagger")
    elif 'ner' not in nlp.pipe_names:
        ner = nlp.create_pipe('ner')
        nlp.add_pipe(ner, last=True)
    # otherwise, get it so we can add labels
    else:
        ner = nlp.get_pipe('ner')

    # add labels
    for _, annotations in train_data:
        for ent in annotations.get('entities'):
            ner.add_label(ent[2])

    # get names of other pipes to disable them during training
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']

    dropout_rates = util.decaying(util.env_opt('dropout_from', 0.2),
                                  util.env_opt('dropout_to', 0.2),
                                  util.env_opt('dropout_decay', 0.005))
    batch_sizes = util.compounding(util.env_opt('batch_from', 1),
                                   util.env_opt('batch_to', 128),
                                   util.env_opt('batch_compound', 1.001))

    optimizer = nlp.begin_training()
    best_epoch = 0
    best_f1 = 0
    for i in range(n_iter):
        print(str(i)+'--'+str(n_iter))
        random.shuffle(train_data)
        count = 0
        losses = {}
        total = len(train_data)

        with nlp.disable_pipes(*other_pipes):  # only train NER
            with tqdm(total=total, leave=True) as pbar:
                for batch in minibatch(train_data, size=batch_sizes):
                    docs, golds = zip(*batch)
                    try:
                        nlp.update(docs, golds, sgd=optimizer,
                               losses=losses, drop=next(dropout_rates))
                        pbar.update(len(batch))
                    except:
                        pass
                    if count % 100 == 0 and count > 0:
                        print('sum loss: %s' % losses['ner'])
                    count += 1

        # save model to output directory
        output_dir_path = Path(output_dir + "/" + str(i))
        if not output_dir_path.exists():
            output_dir_path.mkdir()

        with nlp.use_params(optimizer.averages):
            nlp.tokenizer = original_tokenizer
            nlp.to_disk(output_dir_path)
            print("Saved model to", output_dir_path)

        # test the saved model
        print("Loading from", output_dir_path)
        nlp2 = util.load_model_from_path(output_dir_path)
        nlp2.tokenizer = WhitespaceTokenizer(nlp.vocab)

        metrics = evaluate_ner(nlp2, dev_data)
        if metrics["f1-measure-overall"] > best_f1:
            best_f1 = metrics["f1-measure-overall"]
            best_epoch = i
    # save model to output directory
    best_model_path = Path(output_dir + "/" + "best")
    print(f"Best Epoch: {best_epoch} of {n_iter}")
    if os.path.exists(best_model_path):
        shutil.rmtree(best_model_path)
    shutil.copytree(os.path.join(output_dir, str(best_epoch)),
                    best_model_path)

    # test the saved model
    print("Loading from", best_model_path)
    nlp2 = util.load_model_from_path(best_model_path)
    nlp2.tokenizer = WhitespaceTokenizer(nlp.vocab)

    evaluate_ner(nlp2, dev_data, dump_path=os.path.join(output_dir, "dev_metrics.json"))
    evaluate_ner(nlp2, test_data, dump_path=os.path.join(output_dir, "test_metrics.json"))

In [12]:
import math

nLines = len(df.index)
percentage = 0.70
nTrain = int(nLines * percentage)
nValid = math.floor((nLines - nTrain) / 2)
nTest = nLines - (nTrain + nValid)

train_data = training_data[0:nTrain]
devel_data = training_data[nTrain:nTrain + nValid]
test_data = training_data[nTrain + nValid:nTrain + nValid + nTest]

In [13]:
model_output_dir = '/nfs/gns/literature/Santosh_Tirunagari/GitHub/spacy_models/en-metagenomics-lg/en-core-BGCs-2m-lg'
run_test = False
model_path = '/nfs/gns/literature/Santosh_Tirunagari/pretrained_word_embeddings/models/en-metgenomics-lg/' # None #'en_core_sci_md'
iterations = 10
meta_overrides = '/nfs/gns/literature/Santosh_Tirunagari/GitHub/scispacy/data/EPMC_ner.json'

In [14]:
train_ner(model_output_dir,
              train_data,
              devel_data,
              test_data,
              run_test,
              model_path,
              iterations,
              meta_overrides)

Loaded model '/nfs/gns/literature/Santosh_Tirunagari/pretrained_word_embeddings/models/en-metgenomics-lg/'
0--10


  0%|          | 104/2275086 [00:04<23:47:55, 26.55it/s]

sum loss: 266.6631175563089


  0%|          | 205/2275086 [00:08<24:29:01, 25.81it/s]

sum loss: 406.74073409986056


...

precision-untyped: 0.9705206934106222
recall-untyped: 0.7049064944288962
f1-measure-untyped: 0.8166589926774804
precision-BGC: 0.9705206934106222
recall-BGC: 0.7049064944288962
f1-measure-BGC: 0.8166589926774804
precision-overall: 0.9705206934106222
recall-overall: 0.7049064944288962
f1-measure-overall: 0.8166589926774804


100%|█████████▉| 487034/487519 [24:41<00:01, 267.74it/s]

precision-untyped: 0.970528111430666
recall-untyped: 0.7049631282313199
f1-measure-untyped: 0.8166996248916043
precision-BGC: 0.970528111430666
recall-BGC: 0.7049631282313199
f1-measure-BGC: 0.8166996248916043
precision-overall: 0.970528111430666
recall-overall: 0.7049631282313199
f1-measure-overall: 0.8166996248916043


100%|██████████| 487519/487519 [24:43<00:00, 328.60it/s]


precision-untyped: 		 0.970525303649072
recall-untyped: 		 0.7049581903328016
f1-measure-untyped: 		 0.816695317130953
precision-overall: 		 0.970525303649072
recall-overall: 		 0.7049581903328016
f1-measure-overall: 		 0.816695317130953


In [15]:
model_path = '/nfs/gns/literature/Santosh_Tirunagari/GitHub/spacy_models/en-metagenomics-lg/en-core-BGCs-2m-lg/best'
bgc_nlp = spacy.load(model_path)




In [17]:
text = "Immediately downstream of cumC is found the gene cumD, which shows homology to genes for cytochrome P-450 enzymes: the very recently described NikQ catalyzes the Î²-hydroxylation of histidine during nikkomycin biosynthesis (17), and the product of ORF20 of the chloroeremomycin biosynthetic gene cluster (46) may be involved in the Î²-hydroxylation of tyrosine (17)."
sentence = bgc_nlp(text)
for ent in sentence.ents:
    print([ent.start_char, ent.end_char, ent.text, ent.label_])


[199, 209, 'nikkomycin', 'BGC']
[261, 277, 'chloroeremomycin', 'BGC']
